# Carico i dataset MC

In [120]:
import pandas as pd
import os
from pathlib import Path

def carica_training_dataset():
    """
    Cerca il file Training_datasetMC.csv nelle cartelle tipiche del progetto,
    lo carica, lo pulisce e restituisce un DataFrame con colonne:
    - text
    - label (0/1)
    """

    # 1) Capisco da dove sto eseguendo il notebook
    cwd = Path().resolve()
    print("Current working dir:", cwd)

    # 2) Elenco di possibili percorsi dove potrebbe stare il CSV
    candidate_paths = [
        cwd / "Training_datasetMC.csv",
        cwd / "DataRaw" / "Training_datasetMC.csv",
        cwd.parent / "DataRaw" / "Training_datasetMC.csv",
        cwd.parent / "src" / "DataRaw" / "Training_datasetMC.csv",
    ]

    path_input = None
    for p in candidate_paths:
        if p.exists():
            path_input = p
            break

    if path_input is None:
        raise FileNotFoundError(
            "Non trovo Training_datasetMC.csv. Ho provato questi percorsi:\n" +
            "\n".join(str(p) for p in candidate_paths)
        )

    print("Carico:", path_input)

    # 3) Lettura robusta del CSV (gestisce le virgole dentro le frasi)
    df = pd.read_csv(
        path_input,
        header=None,
        names=["id", "text", "label"],
        quotechar='"',
        sep=",",
        encoding="utf-8",
        engine="python",    # parser più tollerante
        on_bad_lines="skip" # salta eventuali righe rovinate
    )

    print("Shape originale:", df.shape)

    # 4) Rimuovo la colonna ID
    df = df.drop(columns=["id"])

    # 5) Pulizia base del testo
    df["text"] = (
        df["text"]
        .astype(str)
        .str.strip()
        .str.replace(r'^"|"$', "", regex=True)  # rimuove doppi apici ai bordi se presenti
    )

    # 6) Pulizia e conversione della label
    df["label"] = pd.to_numeric(df["label"], errors="coerce")
    df = df.dropna(subset=["label"])
    df["label"] = df["label"].astype(int)

    # 7) Tolgo eventuali righe con testo vuoto
    df = df[df["text"].str.len() > 0]

    # 8) Tolgo eventuali duplicati
    df = df.drop_duplicates(subset=["text", "label"])

    print("Shape pulito:", df.shape)
    return df

train_dfMC = carica_training_dataset()

Current working dir: C:\Users\marco\Desktop\IronyDetection\src\Code
Carico: C:\Users\marco\Desktop\IronyDetection\src\DataRaw\Training_datasetMC.csv
Shape originale: (3996, 3)
Shape pulito: (3995, 2)


## Pulisco il dataset train_MC

In [121]:
# Mescolo completamente le righe del dataset
train_dfMC_shuffled = (
    train_dfMC
    .sample(frac=1, random_state=43)  # frac=1 => prende il 100% delle righe in ordine casuale
    .reset_index(drop=True)           # resetta l'indice dopo lo shuffle
)

train_dfMC = train_dfMC_shuffled


import re


# Regex UNIVERSALE che prende (quasi) tutte le emoji moderne:
emoji_pattern = re.compile(
    "["
    "\U0001F000-\U0001FFFF"  # tutto il blocco multilingue (contiene TUTTE le emoji moderne)
    "\u2600-\u26FF"          # simboli vari (☀️, ☂️ ecc.)
    "\u2700-\u27BF"          # dingbats (✂️, ✌️ ecc.)
    "]+",
    flags=re.UNICODE
)


def pulisci_testo(t):
    t = str(t)

    # 1. rimozione emoji
    t = emoji_pattern.sub(r'', t)

    # 2. minuscolo
    t = t.lower()

    # 3. normalizzazione apostrofi
    t = t.replace("’", "'").replace("‘", "'")

    # 4. rimuove spazi multipli
    t = re.sub(r"\s+", " ", t)

    # 5. rimuove spazi ai bordi
    t = t.strip()

    return t

train_dfMC["text"] = train_dfMC["text"].apply(pulisci_testo)

## Pulisco il dataset test_MC

In [122]:
import pandas as pd
from pathlib import Path
import re
from IPython.display import display, HTML

# ==========================
#  Regex emoji universale
# ==========================
emoji_pattern = re.compile(
    "["
    "\U0001F000-\U0001FFFF"   # quasi tutte le emoji moderne
    "\u2600-\u26FF"           # simboli vari
    "\u2700-\u27BF"           # dingbats
    "]+",
    flags=re.UNICODE
)

# ==========================
#  Pulizia testo MC
# ==========================
def pulisci_testo_mc(t: str) -> str:
    t = str(t)

    # 1) Rimuove emoji
    t = emoji_pattern.sub("", t)

    # 2) Minuscolo
    t = t.lower()

    # 3) Normalizza apostrofi
    t = t.replace("’", "'").replace("‘", "'")

    # 4) Spazi multipli -> uno solo
    t = re.sub(r"\s+", " ", t)

    # 5) Strip finale
    t = t.strip()

    return t

# ==========================
#  Carica TEST MC
# ==========================
def carica_test_dataset_mc():
    """
    Cerca il file Test_datasetMC.csv nelle cartelle tipiche del progetto,
    lo carica, lo pulisce da righe sporche e restituisce un DataFrame con:
      - text
      - label (0/1)
    """

    cwd = Path().resolve()
    print("Current working dir:", cwd)

    filename = "Test_datasetMC.csv"

    candidate_paths = [
        cwd / filename,
        cwd / "DataRaw" / filename,
        cwd.parent / "DataRaw" / filename,
        cwd.parent / "src" / "DataRaw" / filename,
    ]

    path_input = None
    for p in candidate_paths:
        if p.exists():
            path_input = p
            break

    if path_input is None:
        raise FileNotFoundError(
            "Non trovo Test_datasetMC.csv. Ho provato questi percorsi:\n" +
            "\n".join(str(p) for p in candidate_paths)
        )

    print("Carico TEST MC da:", path_input)

    # Lettura robusta del CSV (gestisce virgole dentro le frasi)
    df = pd.read_csv(
        path_input,
        header=None,
        names=["id", "text", "label"],
        quotechar='"',
        sep=",",
        encoding="utf-8",
        engine="python",
        on_bad_lines="skip"
    )

    print("Shape originale test:", df.shape)

    # Rimuovo colonna id
    df = df.drop(columns=["id"])

    # Pulizia base del testo
    df["text"] = (
        df["text"]
        .astype(str)
        .str.strip()
        .str.replace(r'^"|"$', "", regex=True)  # toglie doppi apici ai bordi se presenti
    )

    # Pulizia/convert label
    df["label"] = pd.to_numeric(df["label"], errors="coerce")
    df = df.dropna(subset=["label"])
    df["label"] = df["label"].astype(int)

    # Tolgo righe con testo vuoto
    df = df[df["text"].str.len() > 0]

    # Tolgo duplicati testo+label
    df = df.drop_duplicates(subset=["text", "label"])

    print("Shape pulito test:", df.shape)
    print("Distribuzione label (test):")
    print(df["label"].value_counts())

    return df

# ==========================
#  Carico, mescolo, pulisco, visualizzo
# ==========================

test_dfMC = carica_test_dataset_mc()

# Mescolo le righe del test
test_dfMC = test_dfMC.sample(frac=1, random_state=43).reset_index(drop=True)

# Applico pulizia testo
test_dfMC["text"] = test_dfMC["text"].apply(pulisci_testo_mc)



Current working dir: C:\Users\marco\Desktop\IronyDetection\src\Code
Carico TEST MC da: C:\Users\marco\Desktop\IronyDetection\src\DataRaw\Test_datasetMC.csv
Shape originale test: (938, 3)
Shape pulito test: (938, 2)
Distribuzione label (test):
label
1    469
0    469
Name: count, dtype: int64


## Pulisco il dataset train_ironITA

In [123]:
import pandas as pd
from pathlib import Path

def carica_training_ironita():
    """
    Carica il file training_ironita2018.xlsx, elimina id e topic,
    unisce irony e sarcasm in un'unica label binaria (0/1) e
    restituisce un DataFrame con colonne:
      - text
      - label (1 se ironia o sarcasmo, 0 altrimenti)
    """

    cwd = Path().resolve()
    print("Current working dir:", cwd)

    filename = "training_ironita2018.xlsx"

    # Possibili percorsi (come per MC)
    candidate_paths = [
        cwd / filename,
        cwd / "DataRaw" / filename,
        cwd.parent / "DataRaw" / filename,
        cwd.parent / "src" / "DataRaw" / filename,
    ]

    path_input = None
    for p in candidate_paths:
        if p.exists():
            path_input = p
            break

    if path_input is None:
        raise FileNotFoundError(
            f"Non trovo {filename}. Ho provato questi percorsi:\n" +
            "\n".join(str(p) for p in candidate_paths)
        )

    print("Carico:", path_input)

    # Leggo l'Excel (header sulla prima riga)
    df = pd.read_excel(path_input)

    print("Colonne trovate:", list(df.columns))
    print("Shape originale:", df.shape)

    # Normalizzo i nomi delle colonne (minuscolo, niente spazi)
    df.columns = [c.strip().lower() for c in df.columns]

    # Mi aspetto queste colonne: id, text, irony, sarcasm, topic
    # In caso di nomi leggermente diversi puoi sistemarli qui.
    text_col = "text"
    irony_col = "irony"
    sarcasm_col = "sarcasm"

    # Riempio eventuali NaN con 0 nelle colonne irony/sarcasm
    df[irony_col] = df[irony_col].fillna(0)
    df[sarcasm_col] = df[sarcasm_col].fillna(0)

    # Converto a intero (0/1)
    df[irony_col] = df[irony_col].astype(int)
    df[sarcasm_col] = df[sarcasm_col].astype(int)

    # Nuova label: 1 se almeno uno dei due è 1, altrimenti 0
    df["label"] = ((df[irony_col] == 1) | (df[sarcasm_col] == 1)).astype(int)

    # Costruisco il DataFrame finale: SOLO text + label
    df_out = df[[text_col, "label"]].copy()

    # Tolgo eventuali righe vuote / NaN nel testo
    df_out = df_out.dropna(subset=["text"])
    df_out["text"] = df_out["text"].astype(str).str.strip()
    df_out = df_out[df_out["text"].str.len() > 0]

    # Tolgo duplicati testo+label (facoltativo ma pulito)
    df_out = df_out.drop_duplicates(subset=["text", "label"])

    print("Shape pulito IronITA train:", df_out.shape)
    print("Distribuzione label:")
    print(df_out["label"].value_counts())

    return df_out

train_dfITA = carica_training_ironita()
def mescola_dataset(df, seed=42):
    """
    Restituisce un nuovo DataFrame mescolato completamente.
    seed: per garantire la riproducibilità
    """
    df_shuffled = df.sample(frac=1, random_state=seed).reset_index(drop=True)
    return df_shuffled
train_dfITA = mescola_dataset(train_dfITA)


import re
import html

# Regex UNIVERSALE che prende (quasi) tutte le emoji moderne:
emoji_pattern = re.compile(
    "["
    "\U0001F000-\U0001FFFF"  # tutto il blocco multilingue (contiene TUTTE le emoji moderne)
    "\u2600-\u26FF"          # simboli vari (☀️, ☂️ ecc.)
    "\u2700-\u27BF"          # dingbats (✂️, ✌️ ecc.)
    "]+",
    flags=re.UNICODE
)


def pulisci_tweet_ironita(t: str) -> str:
    t = str(t)

    # 1) Rimuovo i link (http..., https..., www...)
    t = re.sub(r"http\S+|www\.\S+", " ", t)

    # 2) Sostituisco @username con token generico "account"
    t = re.sub(r"@\w+", " account ", t)

    # 3) Tolgo le parentesi quadre [ ]
    t = t.replace("[", " ").replace("]", " ")

    # 4) Rimuovo emoji
    t = emoji_pattern.sub("", t)

    # 5) Tolgo il simbolo # ma tengo la parola del tag
    #    es. "#labuonascuola" -> "labuonascuola"
    t = re.sub(r"#(\w+)", r"\1", t)

    # 6) Minuscolo + normalizzazione apostrofi
    t = t.lower()
    t = t.replace("’", "'").replace("‘", "'")

    # 7) Comprimo spazi multipli e strip finale
    t = re.sub(r"\s+", " ", t)
    t = t.strip()

    # 8) rimuovo date tipo 19/01/2012
    t = re.sub(r"\b\d{1,2}/\d{1,2}/\d{2,4}\b", " ", t)

    # 9) separa numeri e lettere attaccati: 5figli → 5 figli
    t = re.sub(r"(\d)([a-zàèéìòù])", r"\1 \2", t, flags=re.IGNORECASE)
    t = re.sub(r"([a-zàèéìòù])(\d)", r"\1 \2", t, flags=re.IGNORECASE)

    # 0) Decodifica gli artefatti HTML (&gt; -> >, &amp; -> &, ... )
    t = html.unescape(t)

    # 1) Rimuove simboli di markup tipo < > / 
    t = re.sub(r"[<>/]", " ", t)

    # 2) Rimuove frecce, sequenze di trattini, ----->, --->, --- ecc.
    t = re.sub(r"-{2,}|\>{2,}", " ", t)

    # 3) Comprimi eventuali spazi dopo la pulizia
    t = re.sub(r"\s+", " ", t)

    # Rimuove trattini singoli e backslash
    t = re.sub(r"[-\\]", " ", t)

    # Rimuove caratteri non validi / replacement character (�)
    t = t.replace("�", "")



    return t

train_dfITA["text"] = train_dfITA["text"].apply(pulisci_tweet_ironita)


Current working dir: C:\Users\marco\Desktop\IronyDetection\src\Code
Carico: C:\Users\marco\Desktop\IronyDetection\src\DataRaw\training_ironita2018.xlsx
Colonne trovate: ['id', 'text', 'irony', 'sarcasm', 'topic']
Shape originale: (3977, 5)
Shape pulito IronITA train: (3976, 2)
Distribuzione label:
label
1    2022
0    1954
Name: count, dtype: int64


## Pulisco il dataset test_ITA

In [124]:
import pandas as pd
from pathlib import Path

def carica_test_ironita():
    """
    Carica il file test_ironita2018.xlsx (IronyITA test),
    elimina id/topic, unisce irony e sarcasm in un'unica label (0/1)
    e restituisce un DataFrame con colonne:
      - text
      - label
    """

    cwd = Path().resolve()
    print("Current working dir:", cwd)

    filename = "test_ironita2018.xlsx"

    candidate_paths = [
        cwd / filename,
        cwd / "DataRaw" / filename,
        cwd.parent / "DataRaw" / filename,
        cwd.parent / "src" / "DataRaw" / filename,
    ]

    path_input = None
    for p in candidate_paths:
        if p.exists():
            path_input = p
            break

    if path_input is None:
        raise FileNotFoundError(
            f"Non trovo {filename}. Ho provato questi percorsi:\n" +
            "\n".join(str(p) for p in candidate_paths)
        )

    print("Carico TEST IronITA da:", path_input)

    df = pd.read_excel(path_input)
    print("Colonne trovate:", list(df.columns))
    print("Shape originale:", df.shape)

    # normalizza header
    df.columns = [c.strip().lower() for c in df.columns]

    text_col    = "text"
    irony_col   = "irony"
    sarcasm_col = "sarcasm"

    # NaN -> 0
    df[irony_col]   = df[irony_col].fillna(0)
    df[sarcasm_col] = df[sarcasm_col].fillna(0)

    # int 0/1
    df[irony_col]   = df[irony_col].astype(int)
    df[sarcasm_col] = df[sarcasm_col].astype(int)

    # label finale: 1 se irony OR sarcasm
    df["label"] = ((df[irony_col] == 1) | (df[sarcasm_col] == 1)).astype(int)

    # solo text + label
    df_out = df[[text_col, "label"]].copy()

    # pulizia minima strutturale
    df_out = df_out.dropna(subset=["text"])
    df_out["text"] = df_out["text"].astype(str).str.strip()
    df_out = df_out[df_out["text"].str.len() > 0]
    df_out = df_out.drop_duplicates(subset=["text", "label"])

    print("Shape pulito TEST IronITA:", df_out.shape)
    print("Distribuzione label:")
    print(df_out["label"].value_counts())

    return df_out

# Carico il test
test_dfITA = carica_test_ironita()

# Applico la pulizia SOLO al test IronITA
test_dfITA["text"] = test_dfITA["text"].apply(pulisci_tweet_ironita)

def rimuovi_account_iniziali(t: str) -> str:
    """
    Funzione dedicata SOLO al test IronITA.
    Rimuove "account" ripetuti SOLO all'inizio della frase.
    """
    t = str(t).strip()
    t = re.sub(r'^(account\s+)+', '', t).strip()
    return t

test_dfITA["text"] = test_dfITA["text"].apply(rimuovi_account_iniziali)

Current working dir: C:\Users\marco\Desktop\IronyDetection\src\Code
Carico TEST IronITA da: C:\Users\marco\Desktop\IronyDetection\src\DataRaw\test_ironita2018.xlsx
Colonne trovate: ['id', 'text', 'irony', 'sarcasm', 'topic']
Shape originale: (872, 5)
Shape pulito TEST IronITA: (872, 2)
Distribuzione label:
label
0    437
1    435
Name: count, dtype: int64


### Datasets puliti



In [125]:
test_dfMC
train_dfMC
train_dfITA
test_dfITA


text  label
0    prendere i libri in copisteria fare la spesa s...      1
1    ...comunque con una crociera costa se non ti a...      1
2    “ account : ogni ragazza:  "non sono una ragaz...      1
3       “la buona scuola”? fa gli errori di grammatica      0
4    “vi hanno sfrattato? andate al campo rom in un...      0
..                                                 ...    ...
867  voglio aprire una gelateria in cambogia lascia...      0
868  voglio sembrare un ragazzo ma mi piace sembrar...      0
869  wojtyla era pronto alle dimissioni. ma non riu...      1
870  zero operatori educativi dalla provincia, camb...      1
871          zingari.originali rom da circonvallazione      1

[872 rows x 2 columns]

In [126]:
from IPython.display import display, HTML

html_table = train_dfITA.to_html(max_rows=None)
#html_table = test_dfMC.to_html(max_rows=None)
#html_table = test_dfITA.to_html(max_rows=None)
#html_table = train_dfMC.to_html(max_rows=None)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc;">
{html_table}
</div>
"""))

# TOKENIZZAZIONE

In [127]:
import re

# prefissi che vogliamo separare quando c'è l'apostrofo
# (articoli e preposizioni/articoli elisi più comuni)
APOSTROFE_PREFIX = {
    "l",      # l'energia
    "un",     # un'amica
    "d",      # d'annunzio
    "del", "dell",   # dell'abitazione
    "al", "all",     # all'ingresso
    "dal", "dall",   # dall'alba
    "nel", "nell",   # nell'armadio
    "sul", "sull",   # sull'acqua
    "col", "coll",   # coll'amico (più raro)
    "gl"             # gl'inviti (italiano più antiquato, ma per sicurezza)
}

def tokenize(text: str):
    """
    - mantiene la punteggiatura come token (.,!?;:,)
    - mantiene parole con apostrofo come UN solo token, tranne quando
      l'apostrofo segue articoli/preposizioni (dell'abitazione -> ['dell','\'','abitazione'])
    - separa lettere e numeri: idea09 -> ['idea', '09']
    - tratta '...', '..', '.' come token separati
    """
    text = str(text)

    # normalizza apostrofi “strani” in '
    text = text.replace("’", "'").replace("‘", "'")

    pattern = r"""
        \.\.\.+                   |  # tre o più puntini: "..." -> "..."
        \.\.                      |  # due puntini
        \.                        |  # singolo punto
        [a-zA-Zàèéìòù]+(?:'[a-zA-Zàèéìòù]+)? |  # parole con eventuale parte dopo apostrofo
        [0-9]+                    |  # numeri
        [!?;:,]                      # altra punteggiatura singola (no apostrofo)
    """

    raw_tokens = re.findall(pattern, text, flags=re.VERBOSE)

    tokens = []
    for tok in raw_tokens:
        if "'" in tok:
            left, right = tok.split("'", 1)
            # controlla se la parte prima dell'apostrofo è un articolo/preposizione da separare
            if left.lower() in APOSTROFE_PREFIX and right:
                # es: "dell'abitazione" -> ["dell", "'", "abitazione"]
                tokens.append(left)
                tokens.append("'")
                tokens.append(right)
            else:
                # tieni il token intero (es: "c'è", "perché", ecc.)
                tokens.append(tok)
        else:
            tokens.append(tok)

    return tokens

esempio = "oggi ho perso il bus09, che bella idea è stata perdere l'autobus!"
print(tokenize(esempio))

['oggi', 'ho', 'perso', 'il', 'bus', '09', ',', 'che', 'bella', 'idea', 'è', 'stata', 'perdere', 'l', "'", 'autobus', '!']


Aggiungiamo una colonna tokens ai dataset

In [128]:
train_dfMC["tokens"] = train_dfMC["text"].apply(tokenize) 
test_dfMC["tokens"] = test_dfMC["text"].apply(tokenize) 
train_dfITA["tokens"] = train_dfITA["text"].apply(tokenize)
test_dfITA["tokens"] = test_dfITA["text"].apply(tokenize)


In [129]:
df_view_ita = train_dfITA[["text", "tokens", "label"]].copy()
df_view_ita["tokens"] = df_view_ita["tokens"].apply(repr)

html_table_ita = df_view_ita.to_html(max_rows=None, escape=False)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc; font-size:14px;">
{html_table_ita}
</div>
"""))

# Mapping dei tokens e vocabolario

In [130]:
from collections import Counter

def costruisci_vocabolario(datasets):
    """
    Costruisce un vocabolario unico da una LISTA di DataFrame,
    ciascuno contenente la colonna 'tokens'.

    Parametri:
        datasets: lista di DataFrame (es: [train_dfMC, train_dfITA])

    Ritorna:
        vocab: dict token -> {"id": int, "freq": int}
        token2id: dict token -> id
        id2token: dict id -> token
    """

    counter = Counter()

    # --- 1) Conta tutte le frequenze dei token ---
    for df in datasets:
        for tokens in df["tokens"]:
            counter.update(tokens)


    vocab = {}
    token2id = {}
    id2token = {}

    # --- 2) Token speciali ---
    current_id = 0

    vocab["<PAD>"] = {"id": current_id, "freq": 0}
    token2id["<PAD>"] = current_id
    id2token[current_id] = "<PAD>"
    current_id += 1

    vocab["<UNK>"] = {"id": current_id, "freq": 0}
    token2id["<UNK>"] = current_id
    id2token[current_id] = "<UNK>"
    current_id += 1

    # --- 3) Riempio il vocabolario con i token ordinati per frequenza ---
    for token, freq in counter.most_common():
        vocab[token] = {"id": current_id, "freq": freq}
        token2id[token] = current_id
        id2token[current_id] = token
        current_id += 1

    # --- 4) Statistiche sui token rari ---
    rare_1 = sum(1 for tok, f in counter.items() if f == 1)
    rare_2 = sum(1 for tok, f in counter.items() if f == 2)

    print("Token con freq = 1:", rare_1)
    print("Token con freq = 2:", rare_2)
    print("Vocabolario totale (con speciali PAD/UNK):", len(vocab))

    return vocab, token2id, id2token

# costuito su entrambi i dataset di training
vocabolario, token2id, id2token = costruisci_vocabolario([train_dfMC, train_dfITA])

Token con freq = 1: 9096
Token con freq = 2: 2445
Vocabolario totale (con speciali PAD/UNK): 16397


In [131]:
# Visualizza il vocabolario in una tabella HTML scorrevole
vocab_df = pd.DataFrame.from_dict(vocabolario, orient="index").reset_index().rename(columns={"index": "token"})
# assicurati ordine colonne e ordine per id
vocab_df = vocab_df[["token", "id", "freq"]].sort_values("id").reset_index(drop=True)

html_table = vocab_df.to_html(index=False, escape=False)
display(HTML(f"""
<div style="height:400px; overflow-y: scroll; border:1px solid #ccc; font-size:13px;">
{html_table}
</div>
"""))

# salva vocab_df come CSV nella cartella Debug_csv
output_dir = Path("Debug_csv")
output_dir.mkdir(parents=True, exist_ok=True)

out_file = output_dir / "vocab.csv"
vocab_df.to_csv(out_file, index=False, encoding="utf-8")

print("Saved vocabulary CSV to:", out_file)

Saved vocabulary CSV to: Debug_csv\vocab.csv


## Mapping id token

In [132]:
def encode_dataset_add_column(df, token2id, tokens_col="tokens", new_col="tokens_int"):
    """
    Aggiunge una colonna `tokens_int` con la sequenza numerica
    per ogni lista di token nella colonna `tokens`.

    Parametri:
        df        : DataFrame con colonna `tokens`
        token2id  : dict token -> id
        tokens_col: nome colonna token (default: 'tokens')
        new_col   : nome colonna con gli ID (default: 'tokens_int')

    Ritorna:
        nuovo_df  : DataFrame con nuova colonna aggiunta
    """

    unk_id = token2id.get("<UNK>")
    if unk_id is None:
        raise ValueError("Errore: manca <UNK> nel vocabolario.")

    def encode(tokens):
        return [token2id.get(t, unk_id) for t in tokens]

    nuovo_df = df.copy()
    nuovo_df[new_col] = nuovo_df[tokens_col].apply(encode)

    return nuovo_df


train_dfMC_encoded  = encode_dataset_add_column(train_dfMC, token2id)
test_dfMC_encoded   = encode_dataset_add_column(test_dfMC, token2id)

train_dfITA_encoded = encode_dataset_add_column(train_dfITA, token2id)
test_dfITA_encoded  = encode_dataset_add_column(test_dfITA, token2id)


### Aggiungo il padding e la Mask
Frasi da 64 parole fisse , aggiungo il padding fino alla fine  
Padding Mask, vettore della frase che per posizione parola 1 parola vera, 0 padding

In [133]:
PAD_ID = token2id.get("<PAD>", 0)   # di solito 0

def pad_dataset(df, max_len, col_in="tokens_int",
                col_ids="input_ids", col_mask="attention_mask"):
    """
    Aggiunge:
      - input_ids      : lista di lunghezza max_len con padding/troncamento
      - attention_mask : 1 per token reali, 0 per pad
    """
    def pad_sequence(seq):
        seq = list(seq)
        if len(seq) >= max_len:
            seq_cut = seq[:max_len]
            mask    = [1] * max_len
        else:
            pad_len = max_len - len(seq)
            seq_cut = seq + [PAD_ID] * pad_len
            mask    = [1] * len(seq) + [0] * pad_len
        return seq_cut, mask

    df_new = df.copy()
    ids_col  = []
    mask_col = []

    for seq in df_new[col_in]:
        ids, m = pad_sequence(seq)
        ids_col.append(ids)
        mask_col.append(m)

    df_new[col_ids]  = ids_col
    df_new[col_mask] = mask_col

    return df_new


MAX_LEN = 64

train_dfMC_pad   = pad_dataset(train_dfMC_encoded,  MAX_LEN)
test_dfMC_pad    = pad_dataset(test_dfMC_encoded,   MAX_LEN)

train_dfITA_pad  = pad_dataset(train_dfITA_encoded, MAX_LEN)
test_dfITA_pad   = pad_dataset(test_dfITA_encoded,  MAX_LEN)

In [134]:
# Visualizza train_dfMC_pad in una tabella HTML scorrevole
html_table = train_dfMC_pad.to_html(max_rows=None, escape=False)
display(HTML(f"""
<div style="height:400px; overflow-y: scroll; border:1px solid #ccc; font-size:13px;">
{html_table}
</div>
"""))

## Creo il dataset ALL (MC + ITA)

In [135]:
train_MC = train_dfMC_pad    # training set MC 
test_MC  = test_dfMC_pad     # test set MC 
train_ITA = train_dfITA_pad  # training set IronITA 
test_ITA  = test_dfITA_pad   # test set IronITA 


# E creo un terzo set dal unione dei due

# Unione
train_all = pd.concat([train_MC, train_ITA], ignore_index=True)

# Shuffle completo
train_all = train_all.sample(frac=1, random_state=42).reset_index(drop=True)

print("Num train_all:", len(train_all))
train_all.head()



test_all = pd.concat([test_MC, test_ITA], ignore_index=True)

test_all = test_all.sample(frac=1, random_state=42).reset_index(drop=True)

print("Num test_all:", len(test_all))

Num train_all: 7971
Num test_all: 1810


-----------------------------------------------------------------------

# FINE PULIZIA DATASETS

In [136]:
# Tutti i dataset finali pronti:

train_MC = train_dfMC_pad    # training set MC 
test_MC  = test_dfMC_pad     # test set MC 
train_ITA = train_dfITA_pad  # training set IronITA 
test_ITA  = test_dfITA_pad   # test set IronITA 
train_all = train_all        # training set unito MC + IronITA
test_all  = test_all         # test set unito MC + IronITA

# di cui la struttura di ogni DataFrame è:
#   - text            : testo originale pulito
#   - label           : etichetta 0/1
#   - tokens          : lista di token (stringhe)
#   - tokens_int      : lista di token convertiti in ID (interi)
#   - input_ids       : lista di ID token padded/troncata a MAX_LEN
#   - attention_mask : lista di 1/0 per indicare token reali/padding


# vocabolario totale (MC + IronITA)
vocabolario = vocabolario # struttura: dict token -> {"token": String, "id": int, "freq": int}       di cui 0 è <PAD> e 1 è <UNK>

# gli id sono messi in ordine crescente a partire da 0 di frequenza decrescente


-----------------------------------------------------------------

# Trasformiamo il dataset in TENSORE
Una classe specializzata di PYTHORCH

In [137]:
import torch

# Classe specializzata di pytorch, rappresenterà il dataset
class TokenDataset(torch.utils.data.Dataset):

    # passo un dataset
    def __init__(self, df):
        self.input_ids = df["input_ids"].values  # lista di 64 ID_token padded, (basati dal vocabolario totale)
        self.labels = df["label"].values         # etichetta 0/1 per ogni frase (ironico non ironico)
        self.texts = df["text"].values           # testo originale pulito per ogni frase
        self.masks = df["attention_mask"].values # lista di 1/0 per ogni frase (1=token reale, 0=pad)


    # ritorna la lunghezza del dataset (4000)
    def __len__(self):
        return len(self.labels)

    # dato un id frase, torna i TORCH TENSOR corrispondenti
    def __getitem__(self, idx):
        ids = torch.tensor(self.input_ids[idx], dtype=torch.long)   # lista dei 64 ID della frase idx
        label = torch.tensor(self.labels[idx], dtype=torch.float32)  # label 0/1 della frase idx
        text = self.texts[idx] 
        mask = torch.tensor(self.masks[idx], dtype=torch.float32)                                      # testo originale della frase idx
        return ids, label, text, mask
    
    

In [138]:
Tensor_TrainAll = TokenDataset(train_all)
Tensor_TestAll  = TokenDataset(test_all)
Tensor_TrainMC  = TokenDataset(train_MC)
Tensor_TestMC   = TokenDataset(test_MC)
Tensor_TrainITA = TokenDataset(train_ITA)
Tensor_TestITA  = TokenDataset(test_ITA)


In [139]:
ids0, label0, text0, mask0 = Tensor_TrainMC[0] 

print(text0) 
print(ids0)      
print(label0)
print(mask0) 

ogni volta che parte un corteo radicale, il centro città diventa un percorso a ostacoli.
tensor([  60,   83,    5,  146,   11, 1115, 2447,    3,    7,  439,  351,  497,
          11,  904,   12, 7301,    2,    0,    0,    0,    0,    0,    0,    0,
           0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
           0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
           0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
           0,    0,    0,    0])
tensor(1.)
tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])


# Definiamo la classe MODEL

In [140]:
'''
import torch
import torch.nn as nn

# CLASSE MODEL
# rappresenta l'intero modello end-to-end
# nel forwar definisco tutti i passaggi che il mio dataset dovrà fare

class IronyEndToEndModel(nn.Module):
    
    def __init__(self, 
                 dim_vocabolario,      # dimensione del vocabolario (usiamo uno unico per tutti i dataset ITA + MC)
                 dim_wordVector=128,   # dimensione del wordVector (128 feature)
                 dim_frase=64,         # lunghezza massima della frase (64 parole)
                 num_heads=4):         # numero di teste della MHSA    
        super().__init__()


        # Istanzio i layer senza fare il forward

        # EMBEDDING LAYER 
        self.embedding_layer = EmbeddingLayer(      
            dim_vocabolario=dim_vocabolario,
            dim_wordVector=dim_wordVector,
            dim_frase=dim_frase,
            padding_idx=0
        )

        # MHSA LAYER
        self.mhsa = MultiHeadSelfAttention(      
            dim_model=dim_wordVector,
            num_heads=num_heads
        )

        # PRIMO RESIDUALNORM LAYER
        self.residual1 = ResidualLayerNorm(      
            dim_model=dim_wordVector
        )
        

        # FFN LAYER
        self.ffn = PositionWiseFFN(              
            dim_model=dim_wordVector
        )

        # SECONDO RESIDUALNORM LAYER
        self.residual2 = ResidualLayerNorm(      
            dim_model=dim_wordVector
        )

        # MEAN POOLING LAYER
        self.mean_pool = MeanPooling()            


        # CLASSIFICATORE FINALE
        self.classifier = SentenceClassifier(       
            dim_model=dim_wordVector
        )

    # Chiama in automatico i forward di tutti i layer
    def forward(self, input_ids, mask):

        # !! input_ids è un tensore MATRICE (numero di frasi x 64 parole(ID) per frase)
        # 4000x64 se metto tutto il training set
        # 32x64 se metto solo un subset di 32 frasi

        # Embedding Layer 
        embeddings = self.embedding_layer(input_ids) 
    
        # MHSA Layer
        attn_out = self.mhsa(embeddings, mask=mask)

        # Primo ResidualNorm Layer
        z1 = self.residual1(embeddings, attn_out)   
        
        # FFN Layer
        ffn_out = self.ffn(z1)    

        # Secondo ResidualNorm Layer
        z2 = self.residual2(z1, ffn_out)      

        # Mean Pooling Layer
        sent_repr = self.mean_pool(z2, mask)        
        
        # Classificatore Finale
        logits = self.classifier(sent_repr)         
        logits = logits.squeeze(-1)                 

        return logits    # otteniamo le predizioni finali y'
    
    
'''

"\nimport torch\nimport torch.nn as nn\n\n# CLASSE MODEL\n# rappresenta l'intero modello end-to-end\n# nel forwar definisco tutti i passaggi che il mio dataset dovrà fare\n\nclass IronyEndToEndModel(nn.Module):\n    \n    def __init__(self, \n                 dim_vocabolario,      # dimensione del vocabolario (usiamo uno unico per tutti i dataset ITA + MC)\n                 dim_wordVector=128,   # dimensione del wordVector (128 feature)\n                 dim_frase=64,         # lunghezza massima della frase (64 parole)\n                 num_heads=4):         # numero di teste della MHSA    \n        super().__init__()\n\n\n        # Istanzio i layer senza fare il forward\n\n        # EMBEDDING LAYER \n        self.embedding_layer = EmbeddingLayer(      \n            dim_vocabolario=dim_vocabolario,\n            dim_wordVector=dim_wordVector,\n            dim_frase=dim_frase,\n            padding_idx=0\n        )\n\n        # MHSA LAYER\n        self.mhsa = MultiHeadSelfAttention(      

## Definiamo i vari layer

### Embeddings
info parola + info posizione

In [141]:
import math
import torch
import torch.nn as nn

class EmbeddingLayer(nn.Module):


    def __init__(self, dim_vocabolario, dim_wordVector, dim_frase, padding_idx=0):
        super().__init__()

        self.token_embedding = nn.Embedding(
                num_embeddings=dim_vocabolario,   # dim vocabolario
                embedding_dim=dim_wordVector,     # 128
                padding_idx=padding_idx           # id = 0 per il padding
            )     
        # i token <PAD> avranno wordVector = [0.0, 0.0, ..., 0.0] - no informazione
        # però verra sommata l'informazione del posVector anche a loro (standard Transformer)

        self.pos_embedding = nn.Embedding(
                num_embeddings=dim_frase,      # 64
                embedding_dim=dim_wordVector   # 128
        )
      
        self.dim_frase = dim_frase              # 64 
        self.dim_wordVector = dim_wordVector   # 128


    def forward(self, input_ids):
        # nel model è il primo layer, riceve input_ids 
        # cioè una matrice (numero di frasi x 64 parole(ID) per frase)
        # 4000x64 frasi totali oppure 32x64 se subset di 32 frasi

        # Ottengo le dimensioni del subset, e lunghezza frase
        batch_size, seq_len = input_ids.size()  

        # Genera i wordVectors per ogni parola nella frase
        token_emb = self.token_embedding(input_ids)  
        
        # (?)
        positions = torch.arange(seq_len, device=input_ids.device)    
        positions = positions.unsqueeze(0).expand(batch_size, seq_len)  

        # genera i posVectors per ogni posizione nella frase
        pos_emb = self.pos_embedding(positions)
       
        # Ogni parola avrà un vettore (di 128) info parola + info posizione
        # embeddings = token_emb + pos_emb  (questo è il metodo senza normalizzazione)

        # info parola + info posizione con normalizzazione scalare (?)
        embeddings = (token_emb * math.sqrt(self.dim_wordVector)) + pos_emb


        return embeddings

### Multi head self attention

In [142]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import math



class MultiHeadSelfAttention(nn.Module):

    def __init__(self, dim_model=128, num_heads=4):
        super().__init__()

        assert dim_model % num_heads == 0, "dim_model deve essere divisibile per num_heads"

        self.dim_model = dim_model                    
        self.num_heads = num_heads                   
        self.head_dim  = dim_model // num_heads   # feature per head : 128/4 = 32

        # pesi da calcolare
        self.W_q = nn.Linear(dim_model, dim_model) # otteniamo Q = "che tipo di altra parola cerco/affine in una frase?"
        self.W_k = nn.Linear(dim_model, dim_model) # otteniamo K = "che tipo di parola è questa?"
        self.W_v = nn.Linear(dim_model, dim_model) # otteniamo V = "che info porto, quanto pesa quella parola sul contesto?"
        
        self.W_o = nn.Linear(dim_model, dim_model) # trasformazione finale che unisce le varie heads
        


    # viene passato x, dopo embedding layer (per ogni frase ogni parola è un wordVector di 128)
    # x è un tesore 4000x64x128 (numero di frasi x lunghezza frase x dim wordVector)
    def forward(self, x, mask=None):
        
        B, L, D = x.size()   # batch size(4000), lunghezza frase(64), dimensione modello(128)

        # GENERO Q,K,V DALLE MATRICI DEI PESI W_q W_k W_v
        Q = self.W_q(x)  # Q = W_q * X + wq  (sempre 4000x64x128)
        K = self.W_k(x)  # K = W_k * X + wk  (sempre 4000x64x128)
        V = self.W_v(x)  # V = W_v * X + wv  (sempre 4000x64x128)

        # QUI FACCIO LO SPLIT NELLE VARIE HEADS
        Q = Q.view(B, L, self.num_heads, self.head_dim).transpose(1, 2)
        K = K.view(B, L, self.num_heads, self.head_dim).transpose(1, 2)
        V = V.view(B, L, self.num_heads, self.head_dim).transpose(1, 2)
        
        # CALCOLO L'ATTENZIONE A
        scores = torch.matmul(Q, K.transpose(-2, -1))  # calcolo A = Q * K^T  (64x64)
        scores = scores / math.sqrt(self.head_dim)  # normalizzo
        
        # uso la mask => Annullo l'attenzione delle parole sui token di padding
        if mask is not None:
            mask_expanded = mask.unsqueeze(1).unsqueeze(2)
            scores = scores.masked_fill(mask_expanded == 0, float('-inf'))

        # la softmax trasforma i -inf in 0, quindi i padding non avranno influenza su altri token
        A = F.softmax(scores, dim=-1) # applico la softmax, ora l'attenzione è distribuita su tutte le feature


        # CALCOLO L'USCITA M
        M = torch.matmul(A, V) # calcolo M = A * V
        M = M.transpose(1, 2).contiguous().view(B, L, D)
        
        out = self.W_o(M)   #  Out = W_o * M + wo  (4000x64x128)
        
        return out

### Residual e normalizzation

In [143]:
import torch
import torch.nn as nn

# Residual + LayerNorm
class ResidualLayerNorm(nn.Module):
    def __init__(self, dim_model=128): 
        super().__init__()

        self.layer_norm = nn.LayerNorm(dim_model)

    # passo X output del embedding layer e out output del layer precedente (MHSA o FFN)
    def forward(self, x, out):

        # sommo feature per feature,
        # unisco le informazioni del nuovo layer con quello precedente (così non perdo info)
        y = x + out
        
        # normalizzazione layer norm
        z = self.layer_norm(y) 
        # ho i paramtri gamma e beta da addestrare
        
        return z # (4000x64x128)

### Feed Forward Network

In [144]:
import torch
import torch.nn as nn

# PER OGNI PAROLA (input 128 feature) APPLICHIAMO UNA RETE FFN
# FULLY CONNECTED, primo strato di 512 neuroni, e gli applichiamo la relu
# Poi un secondo strato di 128, che sarà l'output finale
# CIOE' LA NUOVA WORDVECTOR DELLA PAROLA, trasformata maggiore espressione

class PositionWiseFFN(nn.Module):
    def __init__(self, dim_model=128, dim_hidden=None):
        super().__init__()
        
        # Versione potenziata, il primo layer espande le feature a 512
        if dim_hidden is None:
            dim_hidden = dim_model * 4   # = 512

        self.linear1 = nn.Linear(dim_model, dim_hidden)
        self.activation = nn.ReLU()     
        self.linear2 = nn.Linear(dim_hidden, dim_model)

    def forward(self, x):
        z = self.linear1(x)      
        h = self.activation(z)
        y = self.linear2(h)      
        return y
    
    # ritorna lo stesso tensore (4000x64x128) ma le parole saranno cambiate


Qui viene riapplicata la seconda Residual layer norm

### Mean Pooling

In [145]:
import torch
import torch.nn as nn

# Obbiettivo è rappresentare una frase non più come una matrice (64x128)
# ma come un vettore (1x128) , che rappresenta la sintesi della frase
# andrò a fare una media delle feature di tutte le parole della frase => 128 feature per frase

class MeanPooling(nn.Module):
    def __init__(self):
        super().__init__()
        

    # viene passato X (4000x64x128) e la mask (4000x64), 
    # deve ritornare un tensore (4000x128), ogni riga è una frase, non una parola
    def forward(self, x, mask):
       
        mask_expanded = mask.unsqueeze(-1)     
        mask_expanded = mask_expanded.to(x.dtype)    

        # moltiplicazione elemento per elemento (non prodotto scalare)
        # e mask_expanded si adatta e diventa 4000x64x128 (ripetendo la maschera su tutta la riga)
        # trasforma in 0 tutti i vettori delle parole padding => non voglio rappresentarle nella media delle feature
        x_masked = x * mask_expanded        
        
        sum_x = x_masked.sum(dim=1)   
        lengths = mask_expanded.sum(dim=1)          

        lengths = torch.clamp(lengths, min=1e-8)
        sent_repr = sum_x / lengths                  

    
        return sent_repr   

### Classificatore 

In [146]:
import torch
import torch.nn as nn

# Alla fine quindi prendiamo la nuova rappresentazione della frase (da 64 a 128 elmenti)
# e la diamo in pasto a un semplice classificatore binario (ironico/non ironico)

# Quindi una rete con 128 input e 1 output (logit)
#  NON VIENE APPLICATA QUA LA SIGMOIDE

class SentenceClassifier(nn.Module):
    def __init__(self, dim_model=128):  
        super().__init__()
        
        # singolo strato Fully Connected
        self.linear = nn.Linear(dim_model, 1) 

        
    def forward(self, x):
        
        logits = self.linear(x)   # un valore reale per ogni frase (4000x1)
        
        return logits

# MODELLO IRONYDETECTION

In [147]:
import torch
import torch.nn as nn

# CLASSE MODEL
# rappresenta l'intero modello end-to-end
# nel forwar definisco tutti i passaggi che il mio dataset dovrà fare

class IronyEndToEndModel(nn.Module):
    
    def __init__(self, 
                 dim_vocabolario,      # dimensione del vocabolario (usiamo uno unico per tutti i dataset ITA + MC)
                 dim_wordVector=128,   # dimensione del wordVector (128 feature)
                 dim_frase=64,         # lunghezza massima della frase (64 parole)
                 num_heads=4):         # numero di teste della MHSA    
        super().__init__()


        # Istanzio i layer senza fare il forward

        # EMBEDDING LAYER 
        self.embedding_layer = EmbeddingLayer(      
            dim_vocabolario=dim_vocabolario,
            dim_wordVector=dim_wordVector,
            dim_frase=dim_frase,
            padding_idx=0
        )

        # MHSA LAYER
        self.mhsa = MultiHeadSelfAttention(      
            dim_model=dim_wordVector,
            num_heads=num_heads
        )

        # PRIMO RESIDUALNORM LAYER
        self.residual1 = ResidualLayerNorm(      
            dim_model=dim_wordVector
        )
        

        # FFN LAYER
        self.ffn = PositionWiseFFN(              
            dim_model=dim_wordVector
        )

        # SECONDO RESIDUALNORM LAYER
        self.residual2 = ResidualLayerNorm(      
            dim_model=dim_wordVector
        )

        # MEAN POOLING LAYER
        self.mean_pool = MeanPooling()            


        # CLASSIFICATORE FINALE
        self.classifier = SentenceClassifier(       
            dim_model=dim_wordVector
        )

    # Chiama in automatico i forward di tutti i layer
    def forward(self, input_ids, mask):

        # !! input_ids è un tensore MATRICE (numero di frasi x 64 parole(ID) per frase)
        # 4000x64 se metto tutto il training set
        # 32x64 se metto solo un subset di 32 frasi

        # Embedding Layer 
        embeddings = self.embedding_layer(input_ids) 
    
        # MHSA Layer
        attn_out = self.mhsa(embeddings, mask=mask)

        # Primo ResidualNorm Layer
        z1 = self.residual1(embeddings, attn_out)   
        
        # FFN Layer
        ffn_out = self.ffn(z1)    

        # Secondo ResidualNorm Layer
        z2 = self.residual2(z1, ffn_out)      

        # Mean Pooling Layer
        sent_repr = self.mean_pool(z2, mask)        
        
        # Classificatore Finale
        logits = self.classifier(sent_repr)         
        logits = logits.squeeze(-1)                 

        return logits    # otteniamo le predizioni finali y'
    

In [148]:
dim_vocabolario = len(vocabolario)
IstanzaModelProva = IronyEndToEndModel(
    dim_vocabolario=dim_vocabolario,
    dim_wordVector=128,
    dim_frase=64,
    num_heads=4
)


In [149]:
# DATO UN MODELLO POSSO ACCEDERE AI SUOI PESI
# model.named_parameters() ritorna un iterabile di (nome_peso/layer, tensore_peso)

def stampa_pesi_modello(model):
    print("ELENCO COMPLETO DEI PESI DEL MODELLO:\n")
    for name, param in model.named_parameters():
        print(f"{name:60s}  shape = {tuple(param.shape)}")

stampa_pesi_modello(IstanzaModelProva)

ELENCO COMPLETO DEI PESI DEL MODELLO:

embedding_layer.token_embedding.weight                        shape = (16397, 128)
embedding_layer.pos_embedding.weight                          shape = (64, 128)
mhsa.W_q.weight                                               shape = (128, 128)
mhsa.W_q.bias                                                 shape = (128,)
mhsa.W_k.weight                                               shape = (128, 128)
mhsa.W_k.bias                                                 shape = (128,)
mhsa.W_v.weight                                               shape = (128, 128)
mhsa.W_v.bias                                                 shape = (128,)
mhsa.W_o.weight                                               shape = (128, 128)
mhsa.W_o.bias                                                 shape = (128,)
residual1.layer_norm.weight                                   shape = (128,)
residual1.layer_norm.bias                                     shape = (128,)
ffn.linear1.

## Dataloader
Divide in subset i dataset mescolando le frasi = **Stocastic gradient**

In [150]:
'''
Tensor_TrainAll = TokenDataset(train_all)
Tensor_TestAll  = TokenDataset(test_all)
Tensor_TrainMC  = TokenDataset(train_MC)
Tensor_TestMC   = TokenDataset(test_MC)
Tensor_TrainITA = TokenDataset(train_ITA)
Tensor_TestITA  = TokenDataset(test_ITA)

'''

from torch.utils.data import DataLoader

# DataLoader per il training MC, aiuta a costruire i subset della dimensione giusta
train_loader_MC = DataLoader(
    Tensor_TrainMC,   
    batch_size=32,    # 32 frasi per volta per subset
    shuffle=True      # frasi mescolate, e non selezionate ordinate
)
test_loader_MC = DataLoader(
    Tensor_TestMC,
    batch_size=32,
    shuffle=False     # nel test set non serve mescolare
)
train_loader_ITA = DataLoader(
    Tensor_TrainITA,
    batch_size=32,
    shuffle=True
)
test_loader_ITA = DataLoader(
    Tensor_TestITA,
    batch_size=32,
    shuffle=False
)
train_loader_ALL = DataLoader(
    Tensor_TrainAll,
    batch_size=32,
    shuffle=True
)
test_loader_ALL = DataLoader(
    Tensor_TestAll,
    batch_size=32,
    shuffle=False
)

#-------------------------------------------------------------------
# vero output da dare al modello :
# Loader = classe contenitore, ma che gestisce i subset in automatico (32 frasi x subset)

loader_trainMC = train_loader_MC
loader_testMC  = test_loader_MC
loader_trainITA = train_loader_ITA
loader_testITA  = test_loader_ITA
loader_trainALL = train_loader_ALL
loader_testALL  = test_loader_ALL

# ADDESTRAMENTO

### Funzione di addestramento
Stampa la funzione di costo media J per ogni epoca (ogni ciclo di tutto il dataset)  
L'obbiettivo è che si riduca il più possibile dopo tot epoche

In [151]:
def train_model(model, train_loader, criterion, optimizer, device, num_epochs=5):
    
    train_losses = []

    for epoch in range(num_epochs):
        print(f"\nEPOCH {epoch+1}")
        model.train()  # modalità training (cambia alcune opzioni di nn.Module)

        running_loss = 0.0

        for i, (batch_ids, batch_labels, batch_texts, batch_mask) in enumerate(train_loader):
            # sposto tutto sul device
            batch_ids    = batch_ids.to(device)          # [B, 64]
            batch_labels = batch_labels.to(device)       # [B]
            batch_mask   = batch_mask.to(device)         # [B, 64]

            # azzero il gradiente
            optimizer.zero_grad()

            # forward: il modello ora vuole anche la mask
            logits = model(batch_ids, batch_mask)        # [B]

            # mi assicuro che le label siano float (0.0 / 1.0)
            labels_flat = batch_labels.float()           # [B]

            # calcolo la loss
            loss = criterion(logits, labels_flat)

            # backward
            loss.backward()

            # aggiornamento pesi
            optimizer.step()

            # logging
            J = loss.item()
            running_loss += J * batch_ids.size(0)

            if i % 50 == 0:
                print(f"  batch {i:3d}  loss = {J:.4f}")

        epoch_loss = running_loss / len(train_loader.dataset)
        print(f"\nLoss media epoca {epoch+1}: {epoch_loss:.4f}")
        train_losses.append(epoch_loss)

    return train_losses


### Istanziamo il modello e addestriamo

In [153]:
import torch
import torch.nn as nn
import torch.optim as optim

# istanziamo il modello, opzione di usare la scheda grafica se disponibile
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = IronyEndToEndModel(
    dim_vocabolario=len(vocabolario),
    dim_wordVector=128,
    dim_frase=64,
    num_heads=4
).to(device)

# istanziamo l'oggetto che gestisce la loss(quindi ha anche J) e calcola i gradienti di J
criterion = nn.BCEWithLogitsLoss()

# istaniziamo l'oggetto che aggiorna i pesi del modello
optimizer = optim.Adam(model.parameters(), lr=1e-3)

num_epochs = 1000

train_losses = train_model(
    model,
    loader_trainALL,
    criterion,
    optimizer,
    device,
    num_epochs=num_epochs
)


EPOCH 1
  batch   0  loss = 0.6782
  batch  50  loss = 0.6317
  batch 100  loss = 0.4740
  batch 150  loss = 0.6355
  batch 200  loss = 0.4419

Loss media epoca 1: 0.6106

EPOCH 2
  batch   0  loss = 0.5147
  batch  50  loss = 0.5009
  batch 100  loss = 0.3082
  batch 150  loss = 0.4199
  batch 200  loss = 0.4734

Loss media epoca 2: 0.5084

EPOCH 3
  batch   0  loss = 0.4311
  batch  50  loss = 0.3811
  batch 100  loss = 0.6113
  batch 150  loss = 0.4845
  batch 200  loss = 0.4426

Loss media epoca 3: 0.4389

EPOCH 4
  batch   0  loss = 0.6531
  batch  50  loss = 0.3540
  batch 100  loss = 0.4677
  batch 150  loss = 0.3717
  batch 200  loss = 0.4123

Loss media epoca 4: 0.4070

EPOCH 5
  batch   0  loss = 0.4114
  batch  50  loss = 0.4788
  batch 100  loss = 0.4491
  batch 150  loss = 0.2906
  batch 200  loss = 0.3746

Loss media epoca 5: 0.3381

EPOCH 6
  batch   0  loss = 0.3378
  batch  50  loss = 0.3737
  batch 100  loss = 0.1584
  batch 150  loss = 0.3080
  batch 200  loss = 0.2

KeyboardInterrupt: 